In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.signal import convolve2d, convolve
import PyQt6.QtCore
import os
from matplotlib.animation import FFMpegWriter
os.environ["QT_API"] = "pyqt6"
%matplotlib qt

In [ ]:
class SimSettings:
    def __init__(self,size,k,F):
        self.Du = 1
        self.Dv = 0.5
        self.dt = 1
        self.size = size
        self.k = k
        self.F = F
        self.kernel = np.array([[.05, .2, .05], [.2, -1, .2], [.05, .2, .05]])
        self.cmap = 'copper'

In [ ]:
### THIS IS THE VERSION WITHOUT 3D PLOTTING (run this cell will run the simulation)

# Parameters
Du, Dv = 1, 0.5  # Diffusion coefficients
k = .06052
F = .03000

# System size
size = 256
dt = 1

# Initial conditions
u = np.ones((size, size))
v = np.zeros((size, size))

half_v = len(v) // 2
v[half_v-30:half_v+30,20:30] = 1
v[half_v-30, 20:70] = 1
v[half_v, 20:70] = 1
v[half_v+30, 20:70] = 1

v[half_v-30:half_v+30, 100:120] = 1
v[half_v-30,100:150] = 1
v[half_v,100:150] = 1
v[half_v-30:half_v, 150] = 1

v[half_v-30:half_v,170:190] = 1
v[half_v:half_v+30, 190:220] = 1
v[half_v-30, 170:220] = 1
v[half_v, 170:220] = 1
v[half_v+30, 170:220] = 1

# Simulation
num_steps = 7500

metadata = dict(title='2D Reaction-Diffusion', artist='Khoi Nguyen', comment=f'k={k}, F={F}')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure(dpi=200)
convolution_matrix = np.array([[.05, .2, .05], [.2, -1, .2], [.05, .2, .05]])
with writer.saving(fig, f"reaction_diffusion_k{k}_F{F}.mp4", dpi=200):
    for step in range(num_steps):
        # Laplacian operator
        laplacian_u = convolve2d(u, convolution_matrix, mode='same', boundary='wrap')
        laplacian_v = convolve2d(v, convolution_matrix, mode='same', boundary='wrap')
    
        # Reaction-diffusion equations
        du = Du * laplacian_u - u * v**2 + F * (1 - u)
        dv = Dv * laplacian_v + u * v**2 - (F + k) * v
    
        # Update concentrations
        u += dt * du
        v += dt * dv
        if step % 50 == 0:
            print(step, end=' ')
            fig.clear()
            plt.imshow(u, cmap='summer', extent=[0, size, 0, size])
            plt.pause(0.001)
            plt.show()
            writer.grab_frame()

In [ ]:
def sim_reaction_diffusion(sim_settings, v, n_steps, intensity=0.2, zlim=(0,1), offset_matrix=None):
    # Initial conditions
    size = sim_settings.size
    Du, Dv = sim_settings.Du, sim_settings.Dv
    F, k = sim_settings.F, sim_settings.k
    dt = sim_settings.dt
    convolution_matrix = sim_settings.kernel
    
    x, y = np.meshgrid(np.arange(1, size + 1), np.arange(1, size+ 1))
    u = np.ones((size, size))

    offset = np.zeros((size,size))
    
    if type(offset_matrix) != type(None):
        print(type(offset_matrix))
        offset = offset_matrix
    
    metadata = dict(title='2D Reaction-Diffusion', artist='Khoi Nguyen', comment=f'k={k}, F={F}')
    writer = FFMpegWriter(fps=15, metadata=metadata)
    fig = plt.figure(figsize=plt.figaspect(0.5))
    cmap = sim_settings.cmap
    
    with writer.saving(fig, f"reaction_diffusion_k{k}_F{F}.mp4", dpi=200):
        for step in range(n_steps):
            # Laplacian operator
            laplacian_u = convolve2d(u, convolution_matrix, mode='same', boundary='wrap')
            laplacian_v = convolve2d(v, convolution_matrix, mode='same', boundary='wrap')
            
            # Reaction-diffusion equations
            du = Du * laplacian_u - u * v**2 + F * (1 - u)
            dv = Dv * laplacian_v + u * v**2 - (F + k) * v
            
            # Update concentrations
            u += dt * du
            v += dt * dv
            u_temp = (u < 0.5) * intensity
        
            if step % 50 == 0:
                print(step, end=' ')
                fig.clear()
                ax1 = fig.add_subplot(1, 2, 2, projection='3d')
                ax1.plot_surface(x, y, offset + u_temp, cmap=cmap, linewidth=0, antialiased=True, rcount=50, ccount=50)
                ax1.set_zlim(zlim[0],zlim[1])
        
                ax2 = fig.add_subplot(1, 2, 1)
                ax2 = plt.imshow(offset + u, cmap=cmap, extent=[0, size, 0, size])
        
                plt.pause(0.01)
                plt.show()
                writer.grab_frame()

In [ ]:
def sim_reaction_diffusion_3d_only(sim_settings, v, n_steps, intensity=0.2, zlim=(0,1), offset_matrix=None, no_neg=True):
    # Initial conditions
    size = sim_settings.size
    Du, Dv = sim_settings.Du, sim_settings.Dv
    F, k = sim_settings.F, sim_settings.k
    dt = sim_settings.dt
    convolution_matrix = sim_settings.kernel
    
    x, y = np.meshgrid(np.arange(1, size + 1), np.arange(1, size+ 1))
    u = np.ones((size, size))

    offset = np.zeros((size,size))
    
    if type(offset_matrix) != type(None):
        print(type(offset_matrix))
        offset = offset_matrix
    
    metadata = dict(title='2D Reaction-Diffusion', artist='Khoi Nguyen', comment=f'k={k}, F={F}')
    writer = FFMpegWriter(fps=15, metadata=metadata)
    fig = plt.figure()
    
    with writer.saving(fig, f"reaction_diffusion_k{k}_F{F}.mp4", dpi=200):
        for step in range(n_steps):
            # Laplacian operator
            laplacian_u = convolve2d(u, convolution_matrix, mode='same', boundary='wrap')
            laplacian_v = convolve2d(v, convolution_matrix, mode='same', boundary='wrap')
            
            # Reaction-diffusion equations
            du = Du * laplacian_u - u * v**2 + F * (1 - u)
            dv = Dv * laplacian_v + u * v**2 - (F + k) * v
            
            # Update concentrations
            u += dt * du
            v += dt * dv
            u_temp = (u < 0.5) * intensity

            surf = offset + u_temp

            if no_neg:
                surf[surf < 0] = 0
        
            if step % 50 == 0:
                print(step, end=' ')
                fig.clear()
                ax1 = fig.add_subplot(projection='3d')
                ax1.plot_surface(x, y, surf, cmap=sim_settings.cmap, linewidth=0, antialiased=True, rcount=150, ccount=150)
                ax1.set_zlim(zlim[0],zlim[1])
        
                plt.pause(0.01)
                plt.show()
                writer.grab_frame()

In [ ]:
def generate_semisphere(rows, cols, r, center_x, center_y):
    # Create a 2D array filled with zeros
    semi_sphere = np.zeros((rows, cols))
    
    # Define the radius of the semi-sphere
    # radius = min(rows, cols) // 2
    
    # Generate the semi-sphere
    for y in range(rows):
        for x in range(cols):
            # Calculate the distance from the center
            distance = np.sqrt((x - center_x)**2 + (y - center_y)**2)
    
            # Check if the point is within the semi-sphere
            if distance <= r:
                # Calculate the corresponding z-axis value for a semi-sphere
                semi_sphere[y, x] = np.sqrt(r**2 - distance**2)
    return semi_sphere

In [ ]:
def semisphere_random(n,grid_size,max_size):
    result = None
    for _ in range(n):
        random_loc = np.random.randint(0,grid_size,size=2)
        random_size = np.random.randint(0,max_size)
        if type(result) == type(None):
            result = generate_semisphere(grid_size,grid_size,random_size,random_loc[0],random_loc[1])
        else:
            result += generate_semisphere(grid_size,grid_size,random_size,random_loc[0],random_loc[1])
    return result

In [ ]:
### ANIMATION 2

k = .05952
F = .03250 # for regular growing cells that connect
# k = .05364
# F = .01634 # for pulsating cells
off = 50
v = np.zeros((size,size))

## Making EPS letters
half_v = len(v)//2
v[half_v-30:half_v+30,20+off:30+off] = 1
v[half_v-30, 20+off:70+off] = 1
v[half_v, 20+off:70+off] = 1
v[half_v+30, 20+off:70+off] = 1

v[half_v-30:half_v+30, 100+off:120+off] = 1
v[half_v-30,100+off:150+off] = 1
v[half_v,100+off:150+off] = 1
v[half_v-30:half_v, 150+off] = 1

v[half_v-30:half_v,170+off:190+off] = 1
v[half_v:half_v+30, 190+off:220+off] = 1
v[half_v-30, 170+off:220+off] = 1
v[half_v, 170+off:220+off] = 1
v[half_v+30, 170+off:220+off] = 1

sim_reaction_diffusion(size, Du, Dv, F, k, dt, convolution_matrix, v, n_steps=10000)

In [ ]:
### ANIMATION 3
k = .05952
F = .03250
size = 256
ani3 = SimSettings(size,k,F)

# x,y = np.meshgrid(np.arange(size), np.arange(size))
# fig = plt.figure()
# ax = fig.add_subplot(projection='3d')
# ax.set_zlim(0,400)
# ax.plot_surface(x,y,semisphere_random(20,size, 100))
# corals = semisphere_random(20,size, 100)

s1 = generate_semisphere(size,size,size//2,size//2,size//2)
v = np.zeros((size,size))
half_v = len(v)//2
v[50:55, 125:130] = 1
v[125:130, 50:55] = 1
v[half_v-5:half_v+5,half_v-5:half_v+5] = 1

sim_reaction_diffusion_3d_only(ani3, v, n_steps=10000, intensity=10, zlim=(0,size),offset_matrix=s1)